In [ ]:
'''
    ****************** HYBRID RECOMMENDATION SYSTEM  **********************
    
This notebook provides implementation of Hybrid Recommendation System for the problem stated in below link. Please refer below 
link to understand the problem statement in better manner.

https://datahack.analyticsvidhya.com/contest/practice-problem-recommendation-engine/

In this notebook -
A. Data is transformed using Feature engineering concepts.
B. Several algorithms in combination has been put up to build the model to predict the 'Attempted_range' for given user and problem id
    a. cosine_similarity
    b. SVD
    c. Baseline
    d. NMF
    e. KNNBaseline item-item similarity
    f. KNNBaseline user-user similarity
    
C. I was able to get the second best accuracy (F1-score) i.e. '0.5103025641' with using KNNBaseline user-user similarity and Cosine
    similarity algorithm in combination. refer below link for leaderboard.

https://datahack.analyticsvidhya.com/contest/practice-problem-recommendation-engine/lb

'''

In [14]:
import pandas as pd
%matplotlib inline
import matplotlib
import matplotlib.pyplot as plt
import numpy as np
from sklearn.metrics.pairwise import pairwise_distances
from sklearn.metrics.pairwise import cosine_similarity

from sklearn.preprocessing import LabelEncoder
from sklearn.metrics import accuracy_score
from sklearn import preprocessing
from statistics import mean
import math

from sklearn.neighbors import NearestNeighbors
from scipy.sparse import csr_matrix
from numpy import array

from surprise import Reader
from surprise import Dataset
from surprise.model_selection import cross_validate
from surprise import NormalPredictor
from surprise import KNNBasic
from surprise import KNNWithMeans
from surprise import KNNWithZScore
from surprise import KNNBaseline
from surprise import SVD
from surprise import BaselineOnly
from surprise import SVDpp
from surprise import NMF
from surprise import SlopeOne
from surprise import CoClustering
from surprise.accuracy import rmse
from surprise import accuracy
from surprise.model_selection import train_test_split

In [3]:
# Part-1  Load the Problem and Users data into dataframe

problems = pd.read_csv('analytics_vidhya_recommendataion_engine_data/problem_data.csv', sep=',', error_bad_lines=False, encoding="latin-1")
users = pd.read_csv('analytics_vidhya_recommendataion_engine_data/user_data.csv', sep=',', error_bad_lines=False, encoding="latin-1")

In [4]:
problems.head()

problem_id level_type  points                                 tags
0  prob_3649          H     NaN                                  NaN
1  prob_6191          A     NaN                                  NaN
2  prob_2020          F     NaN                                  NaN
3   prob_313          A   500.0                greedy,implementation
4   prob_101          A   500.0  constructive algorithms,greedy,math

In [5]:
users.head()

user_id  submission_count  problem_solved  contribution  country  \
0  user_3311                47              40             0      NaN   
1  user_3028                63              52             0    India   
2  user_2268               226             203            -8    Egypt   
3   user_480               611             490             1  Ukraine   
4   user_650               504             479            12   Russia   

   follower_count  last_online_time_seconds  max_rating   rating  \
0               4                1504111645     348.337  330.849   
1              17                1498998165     405.677  339.450   
2              24                1505566052     307.339  284.404   
3              94                1505257499     525.803  471.330   
4               4                1496613433     548.739  486.525   

           rank  registration_time_seconds  
0  intermediate                 1466686436  
1  intermediate                 1441893325  
2      beginner                 1454267603  
3      advanced                 1350720417  
4      advanced                 1395560498

In [6]:
'''
 ***********    Part-2A  - Feature Engineering ********************  

Problems dataframe contains 'tags' column which contains list of values ... to convert into continious value for model training.

A. Get the unique tags from 'Tags' column 
B. Create a new column for each unqiue tag value
C. Fill these column with either 0 or 1 based on that tag presence on that row

'''

problems['tags'] = problems['tags'].fillna('')

unique_tags = []
df_tags = problems['tags']

for tag in problems['tags']:
    tag = str(tag)
    if tag is not '':
        tag_splits = tag.split(',')
        for s in tag_splits:
            if s not in unique_tags:
                unique_tags.append(s)

def chk_row_index_list(row, tag):
    if tag in row['tags']:
        return 1
    else:
        return 0
        
    
for tag in unique_tags:
    problems[tag] = problems.apply(
                lambda x: chk_row_index_list(x, tag), axis=1)
    

# problems = problems.dropna(subset=['level_type'])
problems['level_type'] = problems['level_type'].fillna('A')
problems.points = problems.groupby('level_type')['points'].apply(lambda x: x.fillna(x.mean()))
problems.points = problems.points.fillna(0.0)
problems.drop(['tags'], axis=1, inplace=True)

users.drop(['last_online_time_seconds', 'registration_time_seconds', 'country'], axis=1, inplace=True)

In [7]:
'''
 ***********    Part-2B  - Feature Engineering ********************
 A. Use lable encoder for converting 'Rank' and 'Level_Type' categorical columnn values into continious
 
'''

rank_values = array(users['rank'])
le_rank = preprocessing.LabelEncoder()
users['rank'] = le_rank.fit_transform(users['rank'])
rank_classes = le_rank.classes_

le_level_type = preprocessing.LabelEncoder()
problems['level_type'] = le_level_type.fit_transform(problems['level_type'])
level_classes = le_level_type.classes_

In [8]:
train_submissions = pd.read_csv('analytics_vidhya_recommendataion_engine_data/train_submissions.csv', sep=',', error_bad_lines=False, encoding="latin-1")
tempdf = pd.merge(problems, train_submissions, on='problem_id', how='inner')
final_df = pd.merge(users, tempdf, on='user_id', how='inner')
final_df.head()

user_id  submission_count  problem_solved  contribution  follower_count  \
0  user_3311                47              40             0               4   
1  user_3311                47              40             0               4   
2  user_3311                47              40             0               4   
3  user_3311                47              40             0               4   
4  user_3311                47              40             0               4   

   max_rating   rating  rank problem_id  level_type  ...  *special  geometry  \
0     348.337  330.849     3    prob_75           0  ...         0         0   
1     348.337  330.849     3  prob_3508           0  ...         0         0   
2     348.337  330.849     3  prob_6362           3  ...         0         0   
3     348.337  330.849     3  prob_1308           2  ...         0         0   
4     348.337  330.849     3  prob_1481           1  ...         0         0   

   graph matchings  string suffix structures  fft  matrices  schedules  2-sat  \
0                0                         0    0         0          0      0   
1                0                         0    0         0          0      0   
2                0                         0    0         0          0      0   
3                0                         0    0         0          0      0   
4                0                         0    0         0          0      0   

   chinese remainder theorem  attempts_range  
0                          0               1  
1                          0               1  
2                          0               2  
3                          0               1  
4                          0               1  

[5 rows x 48 columns]

In [9]:
'''
 ***********    Part-2C  - Feature Engineering ********************
 A. Use lable encoder for converting 'user_id' and 'problem_id' categorical columnn values into continious values
 
'''

le_user_id = preprocessing.LabelEncoder()
users['user_id'] = le_user_id.fit_transform(users['user_id'])
final_df['user_id'] = le_user_id.transform(final_df['user_id'])
train_submissions['user_id'] = le_user_id.transform(train_submissions['user_id'])
user_classes = le_user_id.classes_

le_problem_id = preprocessing.LabelEncoder()
problems['problem_id'] = le_problem_id.fit_transform(problems['problem_id'])
final_df['problem_id'] = le_problem_id.transform(final_df['problem_id'])
train_submissions['problem_id'] = le_problem_id.transform(train_submissions['problem_id'])
problem_classes = le_problem_id.classes_

print('after data transformation-')
final_df.head()

after data transformation-


user_id  submission_count  problem_solved  contribution  follower_count  \
0     2570                47              40             0               4   
1     2570                47              40             0               4   
2     2570                47              40             0               4   
3     2570                47              40             0               4   
4     2570                47              40             0               4   

   max_rating   rating  rank  problem_id  level_type  ...  *special  geometry  \
0     348.337  330.849     3        6267           0  ...         0         0   
1     348.337  330.849     3        2788           0  ...         0         0   
2     348.337  330.849     3        5959           3  ...         0         0   
3     348.337  330.849     3         344           2  ...         0         0   
4     348.337  330.849     3         536           1  ...         0         0   

   graph matchings  string suffix structures  fft  matrices  schedules  2-sat  \
0                0                         0    0         0          0      0   
1                0                         0    0         0          0      0   
2                0                         0    0         0          0      0   
3                0                         0    0         0          0      0   
4                0                         0    0         0          0      0   

   chinese remainder theorem  attempts_range  
0                          0               1  
1                          0               1  
2                          0               2  
3                          0               1  
4                          0               1  

[5 rows x 48 columns]

In [10]:
# Part 3- Get the cosine similarity matrix for Problem and User dataframe
problem_cosine_similarity = cosine_similarity(problems)
user_cosine_similarity = cosine_similarity(users)

problem_cosine_similarity

array([[1.        , 0.77813551, 0.91730815, ..., 0.973738  , 0.79231861,
        0.78707369],
       [0.77813551, 1.        , 0.46369623, ..., 0.90069909, 0.99973759,
        0.22500447],
       [0.91730815, 0.46369623, 1.        , ..., 0.80256495, 0.48386933,
        0.96760873],
       ...,
       [0.973738  , 0.90069909, 0.80256495, ..., 1.        , 0.9104142 ,
        0.62596437],
       [0.79231861, 0.99973759, 0.48386933, ..., 0.9104142 , 1.        ,
        0.2472643 ],
       [0.78707369, 0.22500447, 0.96760873, ..., 0.62596437, 0.2472643 ,
        1.        ]])

In [12]:
# Part-4 - Get the list of user_id and problem_id and corresponding indices
users = users.reset_index()
user_ids = users['user_id']
user_indices = pd.Series(users.index, index=users['user_id'])

problems = problems.reset_index()
problem_ids = problems['problem_id']
problem_indices = pd.Series(problems.index, index=problems['problem_id'])

In [ ]:
reader = Reader(rating_scale=(0, 9))
data = Dataset.load_from_df(train_submissions[['user_id', 'problem_id', 'attempts_range']], reader)

trainset, testset = train_test_split(data, test_size=0.25)

In [51]:
'''
    Part 5A - train the model using SVD algoirthm 
'''

svdalgo = SVD(n_factors=160, n_epochs=100, lr_all=0.005, reg_all=0.1, random_state=0)
svdalgo.fit(trainset)
svdpredictions = svdalgo.test(testset[:200])

print(accuracy.rmse(svdpredictions))

RMSE: 0.8900
0.8899748016154547


In [257]:
'''
    Part 5B - train the model using CoClustering algoirthm 
'''

CoClusteringalgo = CoClustering(n_epochs=100, random_state=42)
CoClusteringalgo.fit(trainset)
CoClusteringalgopredictions = CoClusteringalgo.test(testset[:200])

print(accuracy.rmse(CoClusteringalgopredictions))

RMSE: 1.0311
1.0311492681002459


In [ ]:
'''
    Part 5C - train the model using NMF algoirthm 
'''

nmfalgo = NMF(n_factors=160, n_epochs=100, random_state=0)
nmfalgo.fit(trainset)
nmfpredictions = nmfalgo.test(testset[:200])

print(accuracy.rmse(nmfpredictions))

In [208]:
'''
    Part 5D - train the model using KNNBaseline Item-item similarity algoirthm 
'''

sim_options = {'name': 'pearson_baseline', 'user_based': False}
itemAlgo = KNNBaseline(sim_options=sim_options)
itemAlgo.fit(trainset)
itempredictions = itemAlgo.test(testset[:200])
print(accuracy.rmse(itempredictions))

Estimating biases using als...
Computing the pearson_baseline similarity matrix...
Done computing similarity matrix.
RMSE: 1.0146
1.0146300424898553


In [52]:
'''
    Part 5E - train the model using KNNBaseline User-User similarity algoirthm 
'''

sim_options = {'name': 'pearson_baseline', 'user_based': True}
userAlgo = KNNBaseline(sim_options=sim_options)
userAlgo.fit(trainset)
itempredictions = userAlgo.test(testset[:200])
print(accuracy.rmse(itempredictions))

Estimating biases using als...
Computing the pearson_baseline similarity matrix...
Done computing similarity matrix.
RMSE: 0.8877
0.8877278792589097


In [210]:
'''
    Part 5F - train the model using BaselineOnly algoirthm 
'''

bsl_options = {'method': 'als',
               'n_epochs': 5,
               'reg_u': 12,
               'reg_i': 5
               }
baseline_algo = BaselineOnly(bsl_options=bsl_options)
baseline_algo.fit(trainset)
itempredictions = baseline_algo.test(testset[:200])
print(accuracy.rmse(itempredictions))
# cross_validate(baseline_algo, data, measures=['RMSE'], cv=3, verbose=False)

Estimating biases using als...
RMSE: 0.9501
0.9500616452613694


In [ ]:
'''
    Part 6A - Model Prediction using cosine similarity

Following are steps to predict 'attempted_ranges' for given user id and problem id -

A. Get the similar User IDs and Problems IDs for given user id and problem id respectively.

B. If final_df contains given user id and problem id then return its correponding 'attempted_ranges' column value

C. If not, then get the 'attempted_ranges' column value for each combination of user id and similar problem ids from final_df
    and compute mean of all 'attempted_ranges'  values
    
D. If final_df doesn't contain user id and simialar problem ids combination, then get the 'attempted_ranges' column value for each 
    combination of problem id and similar user ids from final_df and compute mean of all 'attempted_ranges'  values

E. if final_df doesn't contain problem id and simialar user id combination then get the 'attempted_ranges' column value for each 
    combination of similar problem ids and similar user ids from final_df and compute mean of all 'attempted_ranges'  values

C. If not, then return default 'attempted_range' value 
    
'''

def get_recommendations(user_id, problem_id):
    user_idx = user_indices[user_id]
    problem_idx = problem_indices[problem_id]
    
    user_sim_scores = list(enumerate(user_cosine_similarity[user_idx]))
    user_sim_scores = sorted(user_sim_scores, key=lambda x: x[1], reverse=True)
    user_sim_scores = user_sim_scores[1:30]
    
    problem_sim_scores = list(enumerate(problem_cosine_similarity[problem_idx]))
    problem_sim_scores = sorted(problem_sim_scores, key=lambda x: x[1], reverse=True)
    problem_sim_scores = problem_sim_scores[1:30]
    
    user_top_indices = [i[0] for i in user_sim_scores]
    
    similar_user_ids = user_ids.iloc[user_top_indices]
    
    total_attempted_range = []
    for userid in similar_user_ids:
        attempted_ranges = final_df[(final_df['user_id'] == userid) & (final_df['problem_id'] == problem_id)]['attempts_range'].values
        if len(attempted_ranges) > 0:
            total_attempted_range.append(attempted_ranges[0])
    
    compute_avg_attempted_range = 0.0
    if len(total_attempted_range) > 0:
        compute_avg_attempted_range = mean(total_attempted_range)
        # print('for', user_id, ' and ', problem_id, ' attemted_range calcualted via user similarity with value: ', compute_avg_attempted_range)
    else:
        problem_top_indices = [i[0] for i in problem_sim_scores]
        similar_problem_ids = problem_ids.iloc[problem_top_indices]
        
        for problemid in similar_problem_ids:
            attempted_ranges = final_df[(final_df['user_id'] == user_id) & (final_df['problem_id'] == problemid)]['attempts_range'].values
            if len(attempted_ranges) > 0:
                total_attempted_range.append(attempted_ranges[0])
        
        if len(total_attempted_range) > 0:
            compute_avg_attempted_range = mean(total_attempted_range)
            # print('for', user_id, ' and ', problem_id, ' attemted_range calcualted via problem similarity with value: ', compute_avg_attempted_range)
        else:
            for userid in similar_user_ids:
                for problemid in similar_problem_ids:
                    attempted_ranges = final_df[(final_df['user_id'] == userid) & (final_df['problem_id'] == problemid)]['attempts_range'].values
                    if len(attempted_ranges) > 0:
                        total_attempted_range.append(attempted_ranges[0])
            
            if len(total_attempted_range) > 0:
                compute_avg_attempted_range = mean(total_attempted_range)
                # print('for', user_id, ' and ', problem_id, ' attemted_range calcualted via user-problem similarity with value: ', compute_avg_attempted_range)
            else:
                print('there is no matching user and problem')
    
    # compute_avg_attempted_range = mean(compute_avg_attempted_range)
    if (float(compute_avg_attempted_range) % 1) >= 0.5:
        compute_avg_attempted_range = math.ceil(compute_avg_attempted_range)
    else:
        compute_avg_attempted_range = math.floor(compute_avg_attempted_range)
    return compute_avg_attempted_range


# Test for single record where user_id is 2570 and problem_id is 6267
print('Predicted Attempted_range value: ', get_recommendations(2570, 6267))

from sklearn.model_selection import train_test_split
train_df, test_df = train_test_split(train_submissions,
                                   test_size=0.20,
                                   random_state=42)
predicted_rating = []

#lets predict for first 10 test records
test1_df = test_df[:10]
for index, row in test1_df.iterrows():
    atempt_range = get_recommendations(row['user_id'], row['problem_id'])
    print('for', row['user_id'], ' and ', row['problem_id'], 'and ', row['attempts_range'], ' attemted_range calcualted with value: ', row['attempts_range'] , ' : ' , atempt_range)
    predicted_rating.append(atempt_range)

test1_df['predicted_rating'] = predicted_rating
test1_df.head()

Predicted Attempted_range value:  1
for 2148  and  6257 and  1  attemted_range calcualted with value:  1  :  1
for 1937  and  2451 and  2  attemted_range calcualted with value:  2  :  1
for 2451  and  751 and  2  attemted_range calcualted with value:  2  :  3
for 3356  and  1292 and  1  attemted_range calcualted with value:  1  :  2
for 3441  and  4675 and  1  attemted_range calcualted with value:  1  :  1
for 1909  and  6299 and  4  attemted_range calcualted with value:  4  :  5
for 611  and  1954 and  1  attemted_range calcualted with value:  1  :  1
for 2253  and  4015 and  2  attemted_range calcualted with value:  2  :  2
for 105  and  2755 and  4  attemted_range calcualted with value:  4  :  1
for 2937  and  1581 and  2  attemted_range calcualted with value:  2  :  1
for 1467  and  2610 and  2  attemted_range calcualted with value:  2  :  1
for 1989  and  1076 and  2  attemted_range calcualted with value:  2  :  2
for 1452  and  3530 and  1  attemted_range calcualted with value:  

for 93  and  1138 and  1  attemted_range calcualted with value:  1  :  2
for 1916  and  5062 and  1  attemted_range calcualted with value:  1  :  1
for 2763  and  4653 and  2  attemted_range calcualted with value:  2  :  1
for 3255  and  2954 and  3  attemted_range calcualted with value:  3  :  1
for 2806  and  598 and  1  attemted_range calcualted with value:  1  :  1
for 557  and  1991 and  2  attemted_range calcualted with value:  2  :  1
for 248  and  2595 and  3  attemted_range calcualted with value:  3  :  2
for 3084  and  2514 and  3  attemted_range calcualted with value:  3  :  1
for 1704  and  2269 and  1  attemted_range calcualted with value:  1  :  2
for 3192  and  5019 and  1  attemted_range calcualted with value:  1  :  1
for 1109  and  5434 and  2  attemted_range calcualted with value:  2  :  2
for 812  and  59 and  4  attemted_range calcualted with value:  4  :  6
for 2976  and  820 and  2  attemted_range calcualted with value:  2  :  3
for 2906  and  5307 and  3  attemt

for 600  and  2372 and  1  attemted_range calcualted with value:  1  :  1
for 2563  and  340 and  1  attemted_range calcualted with value:  1  :  1
for 1929  and  5364 and  1  attemted_range calcualted with value:  1  :  2
for 1710  and  747 and  2  attemted_range calcualted with value:  2  :  1
for 2811  and  4891 and  1  attemted_range calcualted with value:  1  :  1
for 1473  and  2561 and  1  attemted_range calcualted with value:  1  :  2
for 2212  and  1658 and  3  attemted_range calcualted with value:  3  :  1
for 3276  and  5843 and  4  attemted_range calcualted with value:  4  :  1
for 2323  and  785 and  2  attemted_range calcualted with value:  2  :  1
for 1874  and  4952 and  1  attemted_range calcualted with value:  1  :  1
for 2043  and  1795 and  1  attemted_range calcualted with value:  1  :  2
for 3390  and  3210 and  1  attemted_range calcualted with value:  1  :  1
for 258  and  2669 and  2  attemted_range calcualted with value:  2  :  1
for 281  and  5446 and  1  att

for 3393  and  5198 and  1  attemted_range calcualted with value:  1  :  1
for 717  and  3399 and  1  attemted_range calcualted with value:  1  :  2
for 1963  and  3624 and  2  attemted_range calcualted with value:  2  :  2
for 831  and  975 and  1  attemted_range calcualted with value:  1  :  1
for 2129  and  1959 and  1  attemted_range calcualted with value:  1  :  6
for 1912  and  1303 and  1  attemted_range calcualted with value:  1  :  1
for 72  and  4981 and  1  attemted_range calcualted with value:  1  :  2
for 1666  and  3467 and  2  attemted_range calcualted with value:  2  :  1
for 355  and  1157 and  4  attemted_range calcualted with value:  4  :  2
for 2301  and  5852 and  1  attemted_range calcualted with value:  1  :  1
for 251  and  3708 and  1  attemted_range calcualted with value:  1  :  3
for 2513  and  765 and  2  attemted_range calcualted with value:  2  :  1
for 3242  and  6299 and  2  attemted_range calcualted with value:  2  :  1
for 1825  and  5523 and  2  attem

for 3480  and  6504 and  3  attemted_range calcualted with value:  3  :  1
for 2646  and  4816 and  1  attemted_range calcualted with value:  1  :  1
for 100  and  1208 and  1  attemted_range calcualted with value:  1  :  4
for 784  and  1453 and  2  attemted_range calcualted with value:  2  :  2
for 1121  and  5887 and  1  attemted_range calcualted with value:  1  :  2
for 999  and  4133 and  1  attemted_range calcualted with value:  1  :  2
for 1242  and  6176 and  2  attemted_range calcualted with value:  2  :  2
for 353  and  301 and  1  attemted_range calcualted with value:  1  :  1
for 1148  and  751 and  2  attemted_range calcualted with value:  2  :  2
for 2626  and  4150 and  2  attemted_range calcualted with value:  2  :  1
for 398  and  3307 and  2  attemted_range calcualted with value:  2  :  1
for 2549  and  5852 and  1  attemted_range calcualted with value:  1  :  1
for 1090  and  2557 and  1  attemted_range calcualted with value:  1  :  1
for 1222  and  5242 and  1  atte

...

for 770  and  3652 and  1  attemted_range calcualted with value:  1  :  1
for 633  and  2999 and  2  attemted_range calcualted with value:  2  :  1
for 1284  and  2312 and  2  attemted_range calcualted with value:  2  :  2
for 595  and  4903 and  1  attemted_range calcualted with value:  1  :  1
for 958  and  1821 and  1  attemted_range calcualted with value:  1  :  1
for 2037  and  569 and  2  attemted_range calcualted with value:  2  :  1
for 863  and  4262 and  2  attemted_range calcualted with value:  2  :  3
for 1554  and  6133 and  2  attemted_range calcualted with value:  2  :  1
for 3198  and  4451 and  1  attemted_range calcualted with value:  1  :  1
for 264  and  6162 and  1  attemted_range calcualted with value:  1  :  2
for 863  and  1991 and  1  attemted_range calcualted with value:  1  :  1
for 2053  and  5870 and  1  attemted_range calcualted with value:  1  :  1
for 3358  and  5147 and  1  attemted_range calcualted with value:  1  :  2
for 1473  and  3482 and  1  attem

for 11  and  5926 and  1  attemted_range calcualted with value:  1  :  2
for 3551  and  4318 and  2  attemted_range calcualted with value:  2  :  4
for 2274  and  3666 and  3  attemted_range calcualted with value:  3  :  4
for 3135  and  4646 and  2  attemted_range calcualted with value:  2  :  2
for 3495  and  6194 and  1  attemted_range calcualted with value:  1  :  1
for 1591  and  5697 and  1  attemted_range calcualted with value:  1  :  2
for 1172  and  3024 and  1  attemted_range calcualted with value:  1  :  2
for 2498  and  2300 and  2  attemted_range calcualted with value:  2  :  2
for 2587  and  2163 and  3  attemted_range calcualted with value:  3  :  1
for 602  and  3229 and  2  attemted_range calcualted with value:  2  :  1
for 3009  and  2795 and  1  attemted_range calcualted with value:  1  :  1
for 3561  and  4413 and  2  attemted_range calcualted with value:  2  :  1
for 2324  and  2601 and  1  attemted_range calcualted with value:  1  :  1
for 1279  and  2623 and  1  

for 782  and  612 and  1  attemted_range calcualted with value:  1  :  1
for 3184  and  6366 and  1  attemted_range calcualted with value:  1  :  2
for 2961  and  2997 and  1  attemted_range calcualted with value:  1  :  1
for 3163  and  3011 and  1  attemted_range calcualted with value:  1  :  1
for 3248  and  5163 and  2  attemted_range calcualted with value:  2  :  1
for 2997  and  2601 and  1  attemted_range calcualted with value:  1  :  1
for 19  and  2655 and  2  attemted_range calcualted with value:  2  :  2
for 2050  and  6212 and  2  attemted_range calcualted with value:  2  :  3
for 2138  and  4517 and  4  attemted_range calcualted with value:  4  :  1
for 1792  and  5180 and  2  attemted_range calcualted with value:  2  :  2
for 152  and  4889 and  2  attemted_range calcualted with value:  2  :  1
for 2946  and  2347 and  1  attemted_range calcualted with value:  1  :  1
for 1380  and  1950 and  4  attemted_range calcualted with value:  4  :  1
for 320  and  2595 and  1  att

for 2309  and  1109 and  2  attemted_range calcualted with value:  2  :  2
for 1179  and  2456 and  2  attemted_range calcualted with value:  2  :  1
for 157  and  2795 and  4  attemted_range calcualted with value:  4  :  1
there is no matching user and problem
for 2235  and  3383 and  1  attemted_range calcualted with value:  1  :  0
for 2668  and  3203 and  1  attemted_range calcualted with value:  1  :  1
for 2146  and  999 and  2  attemted_range calcualted with value:  2  :  1
for 3098  and  5852 and  1  attemted_range calcualted with value:  1  :  1
for 1162  and  4542 and  1  attemted_range calcualted with value:  1  :  1
for 3468  and  4357 and  1  attemted_range calcualted with value:  1  :  1
for 300  and  439 and  1  attemted_range calcualted with value:  1  :  2
for 536  and  1484 and  1  attemted_range calcualted with value:  1  :  1
for 1000  and  4150 and  1  attemted_range calcualted with value:  1  :  1
for 3030  and  4115 and  1  attemted_range calcualted with value:  

for 1070  and  1094 and  2  attemted_range calcualted with value:  2  :  1
for 716  and  3818 and  1  attemted_range calcualted with value:  1  :  2
for 1099  and  3 and  1  attemted_range calcualted with value:  1  :  1
for 2191  and  4948 and  2  attemted_range calcualted with value:  2  :  1
for 2273  and  4411 and  1  attemted_range calcualted with value:  1  :  3
for 2173  and  2135 and  3  attemted_range calcualted with value:  3  :  1
for 1026  and  5870 and  1  attemted_range calcualted with value:  1  :  1
for 993  and  649 and  1  attemted_range calcualted with value:  1  :  2
for 2810  and  1048 and  6  attemted_range calcualted with value:  6  :  5
there is no matching user and problem
for 1315  and  4956 and  1  attemted_range calcualted with value:  1  :  0


In [247]:
'''
    Part-6B - use cosine similarity and baseline Algorithm to predict the 'attempted_range' value for given user id and problem id
'''

def get_recommendations_baseline(user_id, problem_id):
    user_idx = user_indices[user_id]
    problem_idx = problem_indices[problem_id]
    
    user_sim_scores = list(enumerate(user_cosine_similarity[user_idx]))
    user_sim_scores = sorted(user_sim_scores, key=lambda x: x[1], reverse=True)
    user_sim_scores = user_sim_scores[1:30]
    
    problem_sim_scores = list(enumerate(problem_cosine_similarity[problem_idx]))
    problem_sim_scores = sorted(problem_sim_scores, key=lambda x: x[1], reverse=True)
    problem_sim_scores = problem_sim_scores[1:30]
    
    user_top_indices = [i[0] for i in user_sim_scores]
    similar_user_ids = user_ids.iloc[user_top_indices]
    
    problem_top_indices = [i[0] for i in problem_sim_scores]
    similar_problem_ids = problem_ids.iloc[problem_top_indices]
    
    total_attempted_range = []
    '''
    for problemid in similar_problem_ids:
        total_attempted_range.append(baseline_algo.predict(user_id, problemid).est)
    '''
    
    for userid in similar_user_ids:
        total_attempted_range.append(baseline_algo.predict(userid, problem_id).est)
    
    compute_avg_attempted_range = mean(total_attempted_range)
    if (float(compute_avg_attempted_range) % 1) >= 0.5:
        compute_avg_attempted_range = math.ceil(compute_avg_attempted_range)
    else:
        compute_avg_attempted_range = math.floor(compute_avg_attempted_range)
    
    return compute_avg_attempted_range

In [258]:
'''
    Part-6C - use cosine similarity and coclustering Algorithm to predict the 'attempted_range' value for given user id and problem id
'''

def get_recommendations_coclustering(user_id, problem_id):
    user_idx = user_indices[user_id]
    problem_idx = problem_indices[problem_id]
    
    user_sim_scores = list(enumerate(user_cosine_similarity[user_idx]))
    user_sim_scores = sorted(user_sim_scores, key=lambda x: x[1], reverse=True)
    user_sim_scores = user_sim_scores[1:30]
    
    problem_sim_scores = list(enumerate(problem_cosine_similarity[problem_idx]))
    problem_sim_scores = sorted(problem_sim_scores, key=lambda x: x[1], reverse=True)
    problem_sim_scores = problem_sim_scores[1:30]
    
    user_top_indices = [i[0] for i in user_sim_scores]
    similar_user_ids = user_ids.iloc[user_top_indices]
    
    problem_top_indices = [i[0] for i in problem_sim_scores]
    similar_problem_ids = problem_ids.iloc[problem_top_indices]
    
    total_attempted_range = []
    '''
    for problemid in similar_problem_ids:
        total_attempted_range.append(baseline_algo.predict(user_id, problemid).est)
    '''
    
    for userid in similar_user_ids:
        total_attempted_range.append(CoClusteringalgo.predict(userid, problem_id).est)
    
    compute_avg_attempted_range = mean(total_attempted_range)
    if (float(compute_avg_attempted_range) % 1) >= 0.5:
        compute_avg_attempted_range = math.ceil(compute_avg_attempted_range)
    else:
        compute_avg_attempted_range = math.floor(compute_avg_attempted_range)
    
    return compute_avg_attempted_range

In [239]:
'''
    Part-6D - use cosine similarity and knnbaseline_item Algorithm to predict the 'attempted_range' value for given user id and problem id
'''

def get_recommendations_knnbaseline_item(user_id, problem_id):
    user_idx = user_indices[user_id]
    problem_idx = problem_indices[problem_id]
    
    user_sim_scores = list(enumerate(user_cosine_similarity[user_idx]))
    user_sim_scores = sorted(user_sim_scores, key=lambda x: x[1], reverse=True)
    user_sim_scores = user_sim_scores[1:30]
    
    problem_sim_scores = list(enumerate(problem_cosine_similarity[problem_idx]))
    problem_sim_scores = sorted(problem_sim_scores, key=lambda x: x[1], reverse=True)
    problem_sim_scores = problem_sim_scores[1:30]
    
    user_top_indices = [i[0] for i in user_sim_scores]
    similar_user_ids = user_ids.iloc[user_top_indices]
    
    problem_top_indices = [i[0] for i in problem_sim_scores]
    similar_problem_ids = problem_ids.iloc[problem_top_indices]
    
    total_attempted_range = []
    
    '''
    for problemid in similar_problem_ids:
        total_attempted_range.append(itemAlgo.predict(user_id, problemid).est)
    '''
    
    for userid in similar_user_ids:
        total_attempted_range.append(itemAlgo.predict(userid, problem_id).est)
        
    compute_avg_attempted_range = mean(total_attempted_range)
    if (float(compute_avg_attempted_range) % 1) >= 0.5:
        compute_avg_attempted_range = math.ceil(compute_avg_attempted_range)
    else:
        compute_avg_attempted_range = math.floor(compute_avg_attempted_range)
    
    return compute_avg_attempted_range

In [53]:
'''
    Part-6E - use cosine similarity and knnbaseline_user Algorithm to predict the 'attempted_range' value for given user id and problem id
'''

def get_recommendations_knnbaseline_user(user_id, problem_id):
    user_idx = user_indices[user_id]
    problem_idx = problem_indices[problem_id]
    
    user_sim_scores = list(enumerate(user_cosine_similarity[user_idx]))
    user_sim_scores = sorted(user_sim_scores, key=lambda x: x[1], reverse=True)
    user_sim_scores = user_sim_scores[1:30]
    
    problem_sim_scores = list(enumerate(problem_cosine_similarity[problem_idx]))
    problem_sim_scores = sorted(problem_sim_scores, key=lambda x: x[1], reverse=True)
    problem_sim_scores = problem_sim_scores[1:30]
    
    user_top_indices = [i[0] for i in user_sim_scores]
    similar_user_ids = user_ids.iloc[user_top_indices]
    
    problem_top_indices = [i[0] for i in problem_sim_scores]
    similar_problem_ids = problem_ids.iloc[problem_top_indices]
    
    total_attempted_range = []
    '''
    for problemid in similar_problem_ids:
        total_attempted_range.append(userAlgo.predict(user_id, problemid).est)
    '''
    
    for userid in similar_user_ids:
        total_attempted_range.append(userAlgo.predict(userid, problem_id).est)
        
    compute_avg_attempted_range = mean(total_attempted_range)
    if (float(compute_avg_attempted_range) % 1) >= 0.75:
        compute_avg_attempted_range = math.ceil(compute_avg_attempted_range)
    else:
        compute_avg_attempted_range = math.floor(compute_avg_attempted_range)
    
    return compute_avg_attempted_range

In [235]:
'''
    Part-6F - use cosine similarity and SVD Algorithm to predict the 'attempted_range' value for given user id and problem id
'''

def get_recommendations_svd(user_id, problem_id):
    user_idx = user_indices[user_id]
    problem_idx = problem_indices[problem_id]
    
    user_sim_scores = list(enumerate(user_cosine_similarity[user_idx]))
    user_sim_scores = sorted(user_sim_scores, key=lambda x: x[1], reverse=True)
    user_sim_scores = user_sim_scores[1:30]
    
    problem_sim_scores = list(enumerate(problem_cosine_similarity[problem_idx]))
    problem_sim_scores = sorted(problem_sim_scores, key=lambda x: x[1], reverse=True)
    problem_sim_scores = problem_sim_scores[1:30]
    
    user_top_indices = [i[0] for i in user_sim_scores]
    similar_user_ids = user_ids.iloc[user_top_indices]
    
    problem_top_indices = [i[0] for i in problem_sim_scores]
    similar_problem_ids = problem_ids.iloc[problem_top_indices]
    
    total_attempted_range = []
    '''
    for problemid in similar_problem_ids:
        total_attempted_range.append(svdalgo.predict(user_id, problemid).est)
    '''
    
    for userid in similar_user_ids:
        total_attempted_range.append(svdalgo.predict(userid, problem_id).est)
        
    compute_avg_attempted_range = mean(total_attempted_range)
    if (float(compute_avg_attempted_range) % 1) >= 0.5:
        compute_avg_attempted_range = math.ceil(compute_avg_attempted_range)
    else:
        compute_avg_attempted_range = math.floor(compute_avg_attempted_range)
    
    return compute_avg_attempted_range

In [280]:
'''
    Part-6G - use cosine similarity and NMF Algorithm to predict the 'attempted_range' value for given user id and problem id
'''

def get_recommendations_nmf(user_id, problem_id):
    user_idx = user_indices[user_id]
    problem_idx = problem_indices[problem_id]
    
    user_sim_scores = list(enumerate(user_cosine_similarity[user_idx]))
    user_sim_scores = sorted(user_sim_scores, key=lambda x: x[1], reverse=True)
    user_sim_scores = user_sim_scores[1:30]
    
    problem_sim_scores = list(enumerate(problem_cosine_similarity[problem_idx]))
    problem_sim_scores = sorted(problem_sim_scores, key=lambda x: x[1], reverse=True)
    problem_sim_scores = problem_sim_scores[1:30]
    
    user_top_indices = [i[0] for i in user_sim_scores]
    similar_user_ids = user_ids.iloc[user_top_indices]
    
    problem_top_indices = [i[0] for i in problem_sim_scores]
    similar_problem_ids = problem_ids.iloc[problem_top_indices]
    
    total_attempted_range = []
    '''
    for problemid in similar_problem_ids:
        total_attempted_range.append(nmfalgo.predict(user_id, problemid).est)
    '''
    
    for userid in similar_user_ids:
        total_attempted_range.append(nmfalgo.predict(userid, problem_id).est)
        
    compute_avg_attempted_range = mean(total_attempted_range)
    if (float(compute_avg_attempted_range) % 1) >= 0.66:
        compute_avg_attempted_range = math.ceil(compute_avg_attempted_range)
    else:
        compute_avg_attempted_range = math.floor(compute_avg_attempted_range)
    
    return compute_avg_attempted_range

In [134]:
# Part 7A-  Predict 'attemped_range' for test data via calling SVD algorithm function

train_df, test_df = train_test_split(train_submissions,
                                   test_size=0.20,
                                   random_state=42)

predicted_rating = []
test1_df = test_df
for index, row in test1_df.iterrows():
    atempt_range = get_recommendations_svd(row['user_id'], row['problem_id'])
    predicted_rating.append(atempt_range)

test1_df['predicted_rating'] = predicted_rating

compute_avg_attempted_range in ciel:  2
for 573  and  6203 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 2044  and  5173 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in floor:  1
for 1327  and  4878 and  1  attemted_range calcualted with value:  1  :  1
compute_avg_attempted_range in ciel:  2
for 3159  and  3849 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 1329  and  5317 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 2124  and  735 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 829  and  2685 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 718  and  5462 and  5  attemted_range calcualted with value:  5  :  2
compute_avg_attempted_range in ciel:  2
for 1363  and  4678 and  1  attemted_range 

for 638  and  692 and  3  attemted_range calcualted with value:  3  :  2
compute_avg_attempted_range in ciel:  2
for 2424  and  557 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in floor:  1
for 135  and  672 and  1  attemted_range calcualted with value:  1  :  1
compute_avg_attempted_range in ciel:  2
for 2299  and  2587 and  3  attemted_range calcualted with value:  3  :  2
compute_avg_attempted_range in floor:  1
for 3497  and  3131 and  1  attemted_range calcualted with value:  1  :  1
compute_avg_attempted_range in ciel:  2
for 89  and  5875 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in floor:  2
for 1310  and  1384 and  3  attemted_range calcualted with value:  3  :  2
compute_avg_attempted_range in floor:  2
for 2563  and  1622 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in floor:  2
for 1303  and  4678 and  4  attemted_range calcualted with value:  4  :  2
compute

compute_avg_attempted_range in ciel:  2
for 2603  and  2763 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 249  and  4971 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 3263  and  1935 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 1028  and  5837 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 89  and  3037 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 453  and  3171 and  5  attemted_range calcualted with value:  5  :  2
compute_avg_attempted_range in ciel:  2
for 2181  and  1628 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 483  and  2747 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 1331  and  5364 and  1  attemted_range ca

compute_avg_attempted_range in floor:  2
for 994  and  1743 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 1475  and  6080 and  3  attemted_range calcualted with value:  3  :  2
compute_avg_attempted_range in ciel:  2
for 1872  and  6239 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 2988  and  3934 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 2105  and  4046 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 1971  and  6128 and  3  attemted_range calcualted with value:  3  :  2
compute_avg_attempted_range in ciel:  2
for 1234  and  1206 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 1274  and  2888 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 1756  and  6137 and  1  attemted_ran

compute_avg_attempted_range in floor:  2
for 2831  and  152 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 2468  and  2778 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 3414  and  746 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 1952  and  2675 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 1462  and  1460 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 3498  and  3329 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in floor:  2
for 215  and  404 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 2309  and  10 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 992  and  5200 and  1  attemted_range ca

...

compute_avg_attempted_range in floor:  2
for 339  and  3305 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 2442  and  4595 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 1161  and  2504 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in floor:  1
for 926  and  5817 and  2  attemted_range calcualted with value:  2  :  1
compute_avg_attempted_range in ciel:  2
for 1897  and  5437 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in floor:  2
for 180  and  941 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in floor:  1
for 3497  and  4424 and  2  attemted_range calcualted with value:  2  :  1
compute_avg_attempted_range in floor:  2
for 939  and  3710 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 3294  and  1631 and  2  attemted_ran

compute_avg_attempted_range in ciel:  2
for 3019  and  3736 and  3  attemted_range calcualted with value:  3  :  2
compute_avg_attempted_range in ciel:  2
for 2209  and  4647 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 719  and  3660 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 1278  and  592 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 499  and  6007 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 3048  and  5400 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in floor:  1
for 3532  and  928 and  1  attemted_range calcualted with value:  1  :  1
compute_avg_attempted_range in floor:  1
for 1251  and  4052 and  1  attemted_range calcualted with value:  1  :  1
compute_avg_attempted_range in ciel:  2
for 2196  and  1160 and  1  attemted_range

compute_avg_attempted_range in ciel:  2
for 2077  and  4984 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in floor:  1
for 3365  and  4382 and  2  attemted_range calcualted with value:  2  :  1
compute_avg_attempted_range in ciel:  2
for 1245  and  5627 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 1102  and  4432 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 2753  and  3259 and  6  attemted_range calcualted with value:  6  :  2
compute_avg_attempted_range in ciel:  2
for 3450  and  2542 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 2129  and  881 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 77  and  843 and  3  attemted_range calcualted with value:  3  :  2
compute_avg_attempted_range in ciel:  2
for 1090  and  3441 and  1  attemted_range 

compute_avg_attempted_range in ciel:  2
for 1383  and  4405 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in floor:  1
for 3570  and  4758 and  2  attemted_range calcualted with value:  2  :  1
compute_avg_attempted_range in ciel:  2
for 922  and  5732 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in floor:  2
for 2891  and  4509 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in floor:  2
for 3222  and  5114 and  3  attemted_range calcualted with value:  3  :  2
compute_avg_attempted_range in ciel:  2
for 2790  and  4558 and  1  attemted_range calcualted with value:  1  :  2
compute_avg_attempted_range in ciel:  2
for 2309  and  4340 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 3461  and  757 and  2  attemted_range calcualted with value:  2  :  2
compute_avg_attempted_range in ciel:  2
for 3367  and  292 and  3  attemted_ran

C:\Users\618757\Anaconda3\envs\mypika\lib\site-packages\ipykernel_launcher.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if sys.path[0] == '':


In [141]:
# Part 7B-  Predict 'attemped_range' for test data via calling NMF algorithm function


train_df, test_df = train_test_split(train_submissions,
                                   test_size=0.20,
                                   random_state=42)

predicted_rating = []
test1_df = test_df
for index, row in test1_df.iterrows():
    atempt_range = get_recommendations_nmf(row['user_id'], row['problem_id'])
    print('for', row['user_id'], ' and ', row['problem_id'], 'and ', row['attempts_range'], ' attemted_range calcualted with value: ', row['attempts_range'] , ' : ' , atempt_range)
    predicted_rating.append(atempt_range)

test1_df['predicted_rating'] = predicted_rating

for 573  and  6203 and  1  attemted_range calcualted with value:  1  :  2
for 2044  and  5173 and  2  attemted_range calcualted with value:  2  :  2
for 1327  and  4878 and  1  attemted_range calcualted with value:  1  :  1
for 3159  and  3849 and  1  attemted_range calcualted with value:  1  :  1
for 1329  and  5317 and  2  attemted_range calcualted with value:  2  :  1
for 2124  and  735 and  1  attemted_range calcualted with value:  1  :  1
for 829  and  2685 and  1  attemted_range calcualted with value:  1  :  1
for 718  and  5462 and  5  attemted_range calcualted with value:  5  :  1
for 1363  and  4678 and  1  attemted_range calcualted with value:  1  :  1
for 1371  and  4545 and  1  attemted_range calcualted with value:  1  :  1
for 3364  and  4066 and  2  attemted_range calcualted with value:  2  :  2
for 1507  and  1634 and  4  attemted_range calcualted with value:  4  :  2
for 129  and  1395 and  2  attemted_range calcualted with value:  2  :  2
for 1300  and  2277 and  1  at

for 2488  and  1584 and  1  attemted_range calcualted with value:  1  :  1
for 2109  and  1595 and  1  attemted_range calcualted with value:  1  :  1
for 594  and  874 and  1  attemted_range calcualted with value:  1  :  1
for 1600  and  4322 and  1  attemted_range calcualted with value:  1  :  1
for 1512  and  2887 and  2  attemted_range calcualted with value:  2  :  2
for 1245  and  2402 and  1  attemted_range calcualted with value:  1  :  1
for 1483  and  6176 and  1  attemted_range calcualted with value:  1  :  2
for 716  and  819 and  2  attemted_range calcualted with value:  2  :  1
for 2964  and  1453 and  1  attemted_range calcualted with value:  1  :  2
for 443  and  3114 and  2  attemted_range calcualted with value:  2  :  2
for 178  and  1631 and  2  attemted_range calcualted with value:  2  :  2
for 3356  and  837 and  2  attemted_range calcualted with value:  2  :  1
for 2791  and  4577 and  1  attemted_range calcualted with value:  1  :  2
for 1432  and  5410 and  1  atte

for 994  and  1743 and  2  attemted_range calcualted with value:  2  :  2
for 1475  and  6080 and  3  attemted_range calcualted with value:  3  :  1
for 1872  and  6239 and  2  attemted_range calcualted with value:  2  :  1
for 2988  and  3934 and  1  attemted_range calcualted with value:  1  :  1
for 2105  and  4046 and  2  attemted_range calcualted with value:  2  :  1
for 1971  and  6128 and  3  attemted_range calcualted with value:  3  :  1
for 1234  and  1206 and  1  attemted_range calcualted with value:  1  :  1
for 1274  and  2888 and  1  attemted_range calcualted with value:  1  :  2
for 1756  and  6137 and  1  attemted_range calcualted with value:  1  :  1
for 326  and  6176 and  1  attemted_range calcualted with value:  1  :  2
for 432  and  2854 and  2  attemted_range calcualted with value:  2  :  2
for 3546  and  2146 and  2  attemted_range calcualted with value:  2  :  1
for 717  and  4489 and  2  attemted_range calcualted with value:  2  :  2
for 3146  and  4271 and  1  a

for 570  and  4758 and  2  attemted_range calcualted with value:  2  :  2
for 1647  and  5337 and  1  attemted_range calcualted with value:  1  :  1
for 2397  and  3710 and  1  attemted_range calcualted with value:  1  :  2
for 1119  and  4432 and  1  attemted_range calcualted with value:  1  :  2
for 2155  and  5396 and  2  attemted_range calcualted with value:  2  :  2
for 4  and  288 and  2  attemted_range calcualted with value:  2  :  1
for 1379  and  1231 and  2  attemted_range calcualted with value:  2  :  2
for 258  and  5239 and  5  attemted_range calcualted with value:  5  :  2
for 2284  and  4441 and  2  attemted_range calcualted with value:  2  :  1
for 1927  and  5660 and  1  attemted_range calcualted with value:  1  :  2
for 766  and  1496 and  2  attemted_range calcualted with value:  2  :  1
for 559  and  1160 and  2  attemted_range calcualted with value:  2  :  1
for 723  and  5627 and  2  attemted_range calcualted with value:  2  :  1
for 3081  and  1219 and  1  attemt

for 2864  and  5579 and  2  attemted_range calcualted with value:  2  :  1
for 3507  and  6264 and  1  attemted_range calcualted with value:  1  :  1
for 105  and  756 and  1  attemted_range calcualted with value:  1  :  2
for 1772  and  2869 and  1  attemted_range calcualted with value:  1  :  1
for 1126  and  853 and  1  attemted_range calcualted with value:  1  :  2
for 201  and  5850 and  2  attemted_range calcualted with value:  2  :  2
for 1781  and  94 and  4  attemted_range calcualted with value:  4  :  2
for 1900  and  2257 and  2  attemted_range calcualted with value:  2  :  1
for 631  and  4696 and  2  attemted_range calcualted with value:  2  :  1
for 1075  and  941 and  1  attemted_range calcualted with value:  1  :  2
for 3428  and  6127 and  2  attemted_range calcualted with value:  2  :  1
for 3167  and  5481 and  1  attemted_range calcualted with value:  1  :  2
for 2326  and  663 and  5  attemted_range calcualted with value:  5  :  2
for 2923  and  5151 and  1  attemt

...

for 1788  and  4281 and  1  attemted_range calcualted with value:  1  :  2
for 986  and  117 and  1  attemted_range calcualted with value:  1  :  2
for 464  and  2146 and  2  attemted_range calcualted with value:  2  :  1
for 3386  and  2417 and  3  attemted_range calcualted with value:  3  :  2
for 3013  and  2871 and  1  attemted_range calcualted with value:  1  :  1
for 1971  and  3710 and  1  attemted_range calcualted with value:  1  :  2
for 121  and  3117 and  1  attemted_range calcualted with value:  1  :  2
for 1829  and  1150 and  1  attemted_range calcualted with value:  1  :  2
for 93  and  1375 and  1  attemted_range calcualted with value:  1  :  2
for 1362  and  3548 and  3  attemted_range calcualted with value:  3  :  2
for 1227  and  1001 and  6  attemted_range calcualted with value:  6  :  2
for 736  and  992 and  2  attemted_range calcualted with value:  2  :  2
for 2452  and  2688 and  1  attemted_range calcualted with value:  1  :  2
for 2148  and  114 and  1  attemt

for 3166  and  2104 and  1  attemted_range calcualted with value:  1  :  1
for 1774  and  6174 and  1  attemted_range calcualted with value:  1  :  1
for 485  and  4723 and  2  attemted_range calcualted with value:  2  :  2
for 3126  and  1231 and  1  attemted_range calcualted with value:  1  :  1
for 2322  and  6130 and  1  attemted_range calcualted with value:  1  :  1
for 2424  and  3326 and  2  attemted_range calcualted with value:  2  :  2
for 53  and  5205 and  1  attemted_range calcualted with value:  1  :  1
for 1601  and  1904 and  1  attemted_range calcualted with value:  1  :  2
for 929  and  2287 and  1  attemted_range calcualted with value:  1  :  1
for 1901  and  4363 and  1  attemted_range calcualted with value:  1  :  2
for 2800  and  986 and  1  attemted_range calcualted with value:  1  :  1
for 1245  and  6072 and  1  attemted_range calcualted with value:  1  :  1
for 1081  and  4031 and  1  attemted_range calcualted with value:  1  :  1
for 1045  and  1273 and  4  at

for 1675  and  2542 and  1  attemted_range calcualted with value:  1  :  1
for 752  and  520 and  1  attemted_range calcualted with value:  1  :  1
for 3148  and  4554 and  1  attemted_range calcualted with value:  1  :  2
for 1729  and  984 and  2  attemted_range calcualted with value:  2  :  2
for 3276  and  4927 and  1  attemted_range calcualted with value:  1  :  2
for 1206  and  3007 and  1  attemted_range calcualted with value:  1  :  1
for 2422  and  2397 and  1  attemted_range calcualted with value:  1  :  2
for 2848  and  519 and  1  attemted_range calcualted with value:  1  :  2
for 2410  and  4439 and  3  attemted_range calcualted with value:  3  :  1
for 676  and  3709 and  1  attemted_range calcualted with value:  1  :  1
for 2428  and  3974 and  1  attemted_range calcualted with value:  1  :  2
for 695  and  6098 and  3  attemted_range calcualted with value:  3  :  2
for 685  and  631 and  1  attemted_range calcualted with value:  1  :  1
for 1484  and  1671 and  2  attem

for 3450  and  2542 and  1  attemted_range calcualted with value:  1  :  1
for 2129  and  881 and  1  attemted_range calcualted with value:  1  :  1
for 77  and  843 and  3  attemted_range calcualted with value:  3  :  2
for 1090  and  3441 and  1  attemted_range calcualted with value:  1  :  2
for 3287  and  1273 and  3  attemted_range calcualted with value:  3  :  2
for 2490  and  2060 and  1  attemted_range calcualted with value:  1  :  2
for 2239  and  6287 and  2  attemted_range calcualted with value:  2  :  2
for 978  and  1505 and  2  attemted_range calcualted with value:  2  :  2
for 3139  and  5208 and  1  attemted_range calcualted with value:  1  :  1
for 1780  and  2462 and  1  attemted_range calcualted with value:  1  :  1
for 245  and  899 and  2  attemted_range calcualted with value:  2  :  1
for 3212  and  2397 and  2  attemted_range calcualted with value:  2  :  2
for 862  and  1629 and  2  attemted_range calcualted with value:  2  :  2
for 48  and  292 and  1  attemted

C:\Users\618757\Anaconda3\envs\mypika\lib\site-packages\ipykernel_launcher.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if sys.path[0] == '':


In [187]:
# Part 7C-  Predict 'attemped_range' for test data via calling knnbaseline_item algorithm function


train_df, test_df = train_test_split(train_submissions,
                                   test_size=0.20,
                                   random_state=42)

predicted_rating = []
test1_df = test_df
for index, row in test1_df.iterrows():
    atempt_range = get_recommendations_knnbaseline_item(row['user_id'], row['problem_id'])
    print('for', row['user_id'], ' and ', row['problem_id'], 'and ', row['attempts_range'], ' attemted_range calcualted with value: ', row['attempts_range'] , ' : ' , atempt_range)
    predicted_rating.append(atempt_range)

test1_df['predicted_rating'] = predicted_rating

for 2148  and  6257 and  1  attemted_range calcualted with value:  1  :  1
for 1937  and  2451 and  2  attemted_range calcualted with value:  2  :  2
for 2451  and  751 and  2  attemted_range calcualted with value:  2  :  2
for 3356  and  1292 and  1  attemted_range calcualted with value:  1  :  2
for 3441  and  4675 and  1  attemted_range calcualted with value:  1  :  2
for 1909  and  6299 and  4  attemted_range calcualted with value:  4  :  2
for 611  and  1954 and  1  attemted_range calcualted with value:  1  :  2
for 2253  and  4015 and  2  attemted_range calcualted with value:  2  :  1
for 105  and  2755 and  4  attemted_range calcualted with value:  4  :  2
for 2937  and  1581 and  2  attemted_range calcualted with value:  2  :  2
for 1467  and  2610 and  2  attemted_range calcualted with value:  2  :  2
for 1989  and  1076 and  2  attemted_range calcualted with value:  2  :  2
for 1452  and  3530 and  1  attemted_range calcualted with value:  1  :  1
for 2610  and  5375 and  1  

for 2976  and  820 and  2  attemted_range calcualted with value:  2  :  2
for 2906  and  5307 and  3  attemted_range calcualted with value:  3  :  3
for 452  and  569 and  1  attemted_range calcualted with value:  1  :  2
for 1335  and  3399 and  1  attemted_range calcualted with value:  1  :  2
for 2704  and  4525 and  1  attemted_range calcualted with value:  1  :  2
for 1723  and  3787 and  2  attemted_range calcualted with value:  2  :  2
for 3086  and  6039 and  2  attemted_range calcualted with value:  2  :  2
for 2530  and  4979 and  1  attemted_range calcualted with value:  1  :  2
for 2185  and  5089 and  4  attemted_range calcualted with value:  4  :  2
for 1043  and  859 and  2  attemted_range calcualted with value:  2  :  2
for 2323  and  715 and  1  attemted_range calcualted with value:  1  :  2
for 1737  and  5745 and  2  attemted_range calcualted with value:  2  :  1
for 843  and  6257 and  2  attemted_range calcualted with value:  2  :  2
for 2555  and  2854 and  2  att

for 827  and  6078 and  2  attemted_range calcualted with value:  2  :  2
for 2289  and  2471 and  5  attemted_range calcualted with value:  5  :  2
for 961  and  3183 and  2  attemted_range calcualted with value:  2  :  2
for 2427  and  3934 and  1  attemted_range calcualted with value:  1  :  2
for 21  and  1385 and  1  attemted_range calcualted with value:  1  :  1
for 1444  and  3577 and  1  attemted_range calcualted with value:  1  :  2
for 3467  and  1617 and  3  attemted_range calcualted with value:  3  :  2
for 2004  and  964 and  2  attemted_range calcualted with value:  2  :  2
for 2046  and  797 and  2  attemted_range calcualted with value:  2  :  2
for 265  and  2854 and  2  attemted_range calcualted with value:  2  :  2
for 2182  and  5154 and  1  attemted_range calcualted with value:  1  :  2
for 1818  and  4663 and  1  attemted_range calcualted with value:  1  :  1
for 2643  and  817 and  1  attemted_range calcualted with value:  1  :  2
for 489  and  2815 and  3  attemt

for 756  and  5095 and  1  attemted_range calcualted with value:  1  :  2
for 2581  and  5427 and  5  attemted_range calcualted with value:  5  :  2
for 1022  and  2699 and  1  attemted_range calcualted with value:  1  :  2
for 1801  and  6323 and  2  attemted_range calcualted with value:  2  :  2
for 1642  and  5468 and  1  attemted_range calcualted with value:  1  :  2
for 2335  and  5631 and  2  attemted_range calcualted with value:  2  :  2
for 1711  and  6113 and  1  attemted_range calcualted with value:  1  :  2
for 2060  and  3673 and  6  attemted_range calcualted with value:  6  :  1
for 1260  and  5682 and  2  attemted_range calcualted with value:  2  :  2
for 1267  and  5653 and  2  attemted_range calcualted with value:  2  :  2
for 283  and  4183 and  2  attemted_range calcualted with value:  2  :  2
for 799  and  4075 and  1  attemted_range calcualted with value:  1  :  2
for 1224  and  4721 and  3  attemted_range calcualted with value:  3  :  2
for 2527  and  6437 and  1  

for 1454  and  2173 and  1  attemted_range calcualted with value:  1  :  2
for 3252  and  6227 and  1  attemted_range calcualted with value:  1  :  2
for 1539  and  1283 and  2  attemted_range calcualted with value:  2  :  2
for 591  and  2193 and  2  attemted_range calcualted with value:  2  :  2
for 3399  and  1362 and  1  attemted_range calcualted with value:  1  :  2
for 2063  and  791 and  1  attemted_range calcualted with value:  1  :  2
for 72  and  6395 and  2  attemted_range calcualted with value:  2  :  2
for 2988  and  6200 and  1  attemted_range calcualted with value:  1  :  2
for 843  and  1271 and  1  attemted_range calcualted with value:  1  :  2
for 1372  and  2618 and  3  attemted_range calcualted with value:  3  :  2
for 2868  and  2601 and  1  attemted_range calcualted with value:  1  :  3
for 1130  and  5232 and  1  attemted_range calcualted with value:  1  :  2
for 3285  and  4912 and  2  attemted_range calcualted with value:  2  :  2
for 788  and  4408 and  2  att

...

for 2366  and  5313 and  1  attemted_range calcualted with value:  1  :  2
for 1732  and  1184 and  1  attemted_range calcualted with value:  1  :  2
for 771  and  4208 and  2  attemted_range calcualted with value:  2  :  2
for 3329  and  2618 and  3  attemted_range calcualted with value:  3  :  1
for 344  and  4394 and  3  attemted_range calcualted with value:  3  :  2
for 2211  and  4675 and  1  attemted_range calcualted with value:  1  :  2
for 1462  and  2718 and  2  attemted_range calcualted with value:  2  :  2
for 922  and  1097 and  4  attemted_range calcualted with value:  4  :  2
for 1383  and  6411 and  1  attemted_range calcualted with value:  1  :  2
for 2340  and  4617 and  3  attemted_range calcualted with value:  3  :  2
for 3272  and  875 and  1  attemted_range calcualted with value:  1  :  2
for 960  and  765 and  1  attemted_range calcualted with value:  1  :  2
for 2504  and  3410 and  3  attemted_range calcualted with value:  3  :  2
for 917  and  958 and  2  attem

for 830  and  2702 and  4  attemted_range calcualted with value:  4  :  2
for 2415  and  797 and  1  attemted_range calcualted with value:  1  :  2
for 1521  and  2579 and  1  attemted_range calcualted with value:  1  :  1
for 2150  and  2601 and  1  attemted_range calcualted with value:  1  :  2
for 3154  and  676 and  1  attemted_range calcualted with value:  1  :  2
for 2039  and  5255 and  2  attemted_range calcualted with value:  2  :  2
for 1226  and  6351 and  2  attemted_range calcualted with value:  2  :  2
for 1370  and  75 and  1  attemted_range calcualted with value:  1  :  1
for 777  and  2228 and  1  attemted_range calcualted with value:  1  :  2
for 1703  and  5550 and  2  attemted_range calcualted with value:  2  :  2
for 1473  and  1209 and  1  attemted_range calcualted with value:  1  :  2
for 2170  and  322 and  6  attemted_range calcualted with value:  6  :  2
for 307  and  2646 and  1  attemted_range calcualted with value:  1  :  2
for 3318  and  6439 and  1  attem

for 3234  and  4807 and  2  attemted_range calcualted with value:  2  :  2
for 889  and  2445 and  1  attemted_range calcualted with value:  1  :  2
for 751  and  3569 and  2  attemted_range calcualted with value:  2  :  2
for 1798  and  5513 and  3  attemted_range calcualted with value:  3  :  2
for 736  and  191 and  3  attemted_range calcualted with value:  3  :  2
for 2007  and  659 and  2  attemted_range calcualted with value:  2  :  2
for 913  and  6496 and  5  attemted_range calcualted with value:  5  :  3
for 839  and  5679 and  1  attemted_range calcualted with value:  1  :  2
for 2132  and  2768 and  2  attemted_range calcualted with value:  2  :  2
for 2802  and  5075 and  1  attemted_range calcualted with value:  1  :  2
for 353  and  6256 and  1  attemted_range calcualted with value:  1  :  2
for 2633  and  5073 and  2  attemted_range calcualted with value:  2  :  2
for 314  and  6259 and  1  attemted_range calcualted with value:  1  :  2
for 1919  and  3378 and  1  attemt

for 216  and  4335 and  1  attemted_range calcualted with value:  1  :  2
for 2772  and  4514 and  3  attemted_range calcualted with value:  3  :  2
for 2757  and  5095 and  1  attemted_range calcualted with value:  1  :  2
for 555  and  965 and  1  attemted_range calcualted with value:  1  :  2
for 1272  and  4989 and  1  attemted_range calcualted with value:  1  :  1
for 1739  and  2579 and  1  attemted_range calcualted with value:  1  :  2
for 1776  and  2006 and  2  attemted_range calcualted with value:  2  :  2
for 2551  and  6358 and  2  attemted_range calcualted with value:  2  :  2
for 3313  and  1594 and  1  attemted_range calcualted with value:  1  :  2
for 676  and  667 and  2  attemted_range calcualted with value:  2  :  2
for 2769  and  1171 and  1  attemted_range calcualted with value:  1  :  2
for 1051  and  6069 and  2  attemted_range calcualted with value:  2  :  2
for 2355  and  6275 and  3  attemted_range calcualted with value:  3  :  2
for 2883  and  3920 and  1  at

C:\Users\618757\Anaconda3\envs\mypika\lib\site-packages\ipykernel_launcher.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  if sys.path[0] == '':


In [189]:
#Part 8- Use F1 Score to calculate the model accuracy

from sklearn import metrics

accuracy_score = metrics.accuracy_score(test1_df['predicted_rating'], test1_df['attempts_range'])
precision_score = metrics.precision_score(test1_df['predicted_rating'], test1_df['attempts_range'], average='weighted')
recall_score = metrics.recall_score(test1_df['predicted_rating'], test1_df['attempts_range'], average='weighted')
f1_score = metrics.f1_score(test1_df['predicted_rating'], test1_df['attempts_range'], average='weighted')

print('accuracy_score: ', accuracy_score)
print('precision_score: ', precision_score)
print('recall_score: ', recall_score)
print('f1_score:: ', f1_score)

accuracy_score:  0.34804726488296467
precision_score:  0.8289046374634128
recall_score:  0.34804726488296467
f1_score::  0.4361536838382517


In [54]:
#Part-9 -  Load the test data against which model is going to be vvalidated

test = pd.read_csv('analytics_vidhya_recommendataion_engine_data/test_submissions_NeDLEvX.csv', sep=',', error_bad_lines=False, encoding="latin-1")
sample_submission = pd.read_csv('analytics_vidhya_recommendataion_engine_data/sample_submissions_wbscxqU.csv', sep=',', error_bad_lines=False, encoding="latin-1")

test['problem_id'] = le_problem_id.transform(test['problem_id'])
test['user_id'] = le_user_id.transform(test['user_id'])

sample_submission['ID'] = test['ID']

In [55]:
#Part-10 -  Use knnbaseline_user algorithm for prediction and export the result into CSV file
predicted_attempt_range = []
for index, row in test.iterrows():
    attempt_range = get_recommendations_knnbaseline_user(row['user_id'], row['problem_id'])
    predicted_attempt_range.append(attempt_range)

sample_submission['attempts_range'] = predicted_attempt_range
export_csv = sample_submission.to_csv (r'test_predictions_knnbaseline_user_75_1.csv', sep=',', index = None, header=True)